The data is from the hiPSC single cell image dataset from the Allen Institute for Cell Science: https://open.quiltdata.com/b/allencell/packages/aics/hipsc_single_cell_image_dataset. Original publication of the data: 

Viana, M.P., Chen, J., Knijnenburg, T.A. et al. Integrated intracellular organization and its variations in human iPS cells. Nature 613, 345–354 (2023). https://doi.org/10.1038/s41586-022-05563-7

In [1]:
# you need quilt3 package to download the data:
! pip install quilt3


[notice] A new release of pip is available: 23.0.1 -> 23.1.2
[notice] To update, run: pip install --upgrade pip


In [2]:
import pandas as pd
import quilt3
from pathlib import Path
from aicsimageio import AICSImage
from aicsimageio.writers import OmeTiffWriter
from random import random

In [3]:
# turn off pandas parser warnings
import warnings
warnings.simplefilter(action='ignore', category=FutureWarning)
# tunr off ome_types parser warning
warnings.filterwarnings("ignore", category=FutureWarning)

In [4]:
# set parameters

# which cell line to download: in the paper, we tested on four nuclear structures:
# - fibrillarin (cline = "FBL")
# - nucleophosmin (cline = "NPM1")
# - lamin b1 (cline = "LMNB1")
# - histon H2B (cline = "HIST1H2BJ")
cline = "FBL"
num_samples_per_cell_line = 500 # with roughly 80/20 training/validation split 

# set up path 3D
parent_path_3d = Path("./data/labelfree3D") / f"{cline}"
parent_path_3d.mkdir(exist_ok=True,parents=True)
raw_path_3d = parent_path_3d / Path("download")
raw_path_3d.mkdir(exist_ok=True)
train_path_3d = parent_path_3d / Path("train")
train_path_3d.mkdir(exist_ok=True)
holdout_path_3d = parent_path_3d / Path("holdout")
holdout_path_3d.mkdir(exist_ok=True)

# set up path 2D
parent_path_2d = Path("./data/labelfree2D") / f"{cline}"
parent_path_2d.mkdir(exist_ok=True,parents=True)
# raw_path_2d = parent_path_2d / Path("download")
# raw_path_2d.mkdir(exist_ok=True)
train_path_2d = parent_path_2d / Path("train")
train_path_2d.mkdir(exist_ok=True)
holdout_path_2d = parent_path_2d / Path("holdout")
holdout_path_2d.mkdir(exist_ok=True)

In [16]:
# connect to quilt and load meta table
pkg = quilt3.Package.browse(
    "aics/hipsc_single_cell_image_dataset", registry="s3://allencell"
)
meta_df_obj = pkg["metadata.csv"]
meta_df_obj.fetch(parent_path_3d / "meta.csv")
meta_df = pd.read_csv(parent_path_3d / "meta.csv")

# fetch the data of the specific cell line
meta_df_line = meta_df.query("structure_name==@cline")

# collapse the data table based on FOVId
meta_df_line.drop_duplicates(subset="FOVId", inplace=True)

# reset index
meta_df_line.reset_index(drop=True, inplace=True)

Loading manifest: 100%|██████████| 484465/484465 [00:12<00:00, 38.1k/s]
100%|██████████| 1.69G/1.69G [00:45<00:00, 37.6MB/s] 
/tmp/ipykernel_2232603/1716656791.py:7: DtypeWarning: Columns (33) have mixed types. Specify dtype option on import or set low_memory=False.
  meta_df = pd.read_csv(parent_path_3d / "meta.csv")
/tmp/ipykernel_2232603/1716656791.py:13: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  meta_df_line.drop_duplicates(subset="FOVId", inplace=True)


In [17]:
# download the images and re-slice into input (BF) and ground truth (fluorescent) images
for row in meta_df_line.itertuples():
    if row.Index >= num_samples_per_cell_line:
        break
    
    # fetch the raw image (multi-channel)
    subdir_name = row.fov_path.split("/")[0]
    file_name = row.fov_path.split("/")[1]

    local_fn = raw_path_3d / f"{row.FOVId}_original.tiff"
    pkg[subdir_name][file_name].fetch(local_fn)

    # extract the bf and structures channel
    reader = AICSImage(local_fn)
    bf_img = reader.get_image_data(
        "ZYX", C=row.ChannelNumberBrightfield, S=0, T=0
    )
    str_img = reader.get_image_data(
        "ZYX", C=row.ChannelNumberStruct, S=0, T=0
    )

    if random() < 0.2:
        data_path_3d = holdout_path_3d
        data_path_2d = holdout_path_2d
    else:
        data_path_3d = train_path_3d
        data_path_2d = train_path_2d

    im_fn = data_path_3d / f"{row.FOVId}_IM.tiff"
    gt_fn = data_path_3d / f"{row.FOVId}_GT.tiff"
    OmeTiffWriter.save(bf_img, im_fn, dim_order="ZYX")
    OmeTiffWriter.save(str_img, gt_fn, dim_order="ZYX")
    
    # extract the middle slice from each 3D image
    middle_slice_index = bf_img.shape[0] // 2
    bf_img_2d = bf_img[middle_slice_index, :, :]
    str_img_2d = str_img[middle_slice_index, :, :]
    im_fn = data_path_2d / f"{row.FOVId}_IM.tiff"
    gt_fn = data_path_2d / f"{row.FOVId}_GT.tiff"
    OmeTiffWriter.save(bf_img_2d, im_fn, dim_order="YX")
    OmeTiffWriter.save(str_img_2d, gt_fn, dim_order="YX")


100%|██████████| 384M/384M [00:15<00:00, 24.8MB/s]  
100%|██████████| 378M/378M [00:18<00:00, 20.4MB/s]  
100%|██████████| 379M/379M [00:15<00:00, 25.2MB/s]  
100%|██████████| 385M/385M [00:15<00:00, 25.1MB/s]  
100%|██████████| 378M/378M [00:15<00:00, 23.9MB/s]  
100%|██████████| 387M/387M [00:18<00:00, 21.4MB/s]  
100%|██████████| 374M/374M [00:15<00:00, 24.2MB/s]  
100%|██████████| 385M/385M [00:16<00:00, 23.7MB/s]  
100%|██████████| 385M/385M [00:19<00:00, 19.8MB/s]  
100%|██████████| 381M/381M [00:18<00:00, 20.8MB/s]  
100%|██████████| 391M/391M [00:14<00:00, 27.8MB/s]  
100%|██████████| 377M/377M [00:14<00:00, 25.5MB/s]  
100%|██████████| 384M/384M [00:19<00:00, 19.7MB/s]  
100%|██████████| 375M/375M [00:13<00:00, 27.3MB/s]  
100%|██████████| 379M/379M [00:15<00:00, 24.3MB/s]  
100%|██████████| 377M/377M [00:11<00:00, 32.8MB/s]  
100%|██████████| 376M/376M [00:13<00:00, 28.2MB/s]  
100%|██████████| 384M/384M [00:16<00:00, 23.4MB/s]  
100%|██████████| 385M/385M [00:17<00:00, 22.4M

In [28]:
# you may remove the download folder now.
from shutil import rmtree
import os
rmtree(raw_path_3d)
os.remove(parent_path_3d / "meta.csv")


In [34]:
import shutil

file_names = [f.name for f in Path('/mnt/eternus/users/Jan/data/CompressAI/examples/data/labelfree3D/FBL/train/').glob('*') if f.is_file()]

for path in Path('/mnt/eternus/users/Jan/data/CompressAI/examples/data/labelfree2D/FBL/holdout/').glob('*.tiff'):
    if path.name in file_names:
        # Use the shutil.move() function to move the file
        print(path)
        shutil.move(path, '/mnt/eternus/users/Jan/data/CompressAI/examples/data/labelfree2D/FBL/train/')

/mnt/eternus/users/Jan/data/CompressAI/examples/data/labelfree2D/FBL/holdout/7622_IM.tiff
/mnt/eternus/users/Jan/data/CompressAI/examples/data/labelfree2D/FBL/holdout/7622_GT.tiff
/mnt/eternus/users/Jan/data/CompressAI/examples/data/labelfree2D/FBL/holdout/7624_IM.tiff
/mnt/eternus/users/Jan/data/CompressAI/examples/data/labelfree2D/FBL/holdout/7624_GT.tiff
/mnt/eternus/users/Jan/data/CompressAI/examples/data/labelfree2D/FBL/holdout/7626_IM.tiff
/mnt/eternus/users/Jan/data/CompressAI/examples/data/labelfree2D/FBL/holdout/7626_GT.tiff
/mnt/eternus/users/Jan/data/CompressAI/examples/data/labelfree2D/FBL/holdout/7628_IM.tiff
/mnt/eternus/users/Jan/data/CompressAI/examples/data/labelfree2D/FBL/holdout/7628_GT.tiff
/mnt/eternus/users/Jan/data/CompressAI/examples/data/labelfree2D/FBL/holdout/7630_IM.tiff
/mnt/eternus/users/Jan/data/CompressAI/examples/data/labelfree2D/FBL/holdout/7630_GT.tiff
/mnt/eternus/users/Jan/data/CompressAI/examples/data/labelfree2D/FBL/holdout/7632_IM.tiff
/mnt/etern

# Classic Compression

In [5]:
### Defining compression method (by r/w tmp file)
import tifffile
import os

def wasteful_compression(img, compression):
    try:
        os.remove('/mnt/eternus/users/Jan/code/temp.tiff')
    except OSError:
        pass
    tifffile.imwrite(
         './temp.tiff',
         img,
         bigtiff=True,
         photometric='minisblack',
         planarconfig='separate',
         tile=(16, 16),
         compression=compression,
         compressionargs={'level': 8},
         predictor=True,
         metadata={'axes': 'YX'}
        )
    sample_path = Path("./temp.tiff")
    reader = AICSImage(sample_path)
    img = reader.get_image_data('YX') 
    return img

compression_techniques = ['JPEGXR','JPEG_2000_LOSSY','LERC']

In [6]:
### Compression with classic techniques and appending 'original' 'method'
import shutil

def compress_dir(compression, path, copy_gt=True):
    output_path = path / Path(compression)
    output_path.mkdir(parents=True, exist_ok=True)
    for image_path in path.glob('*.tiff'):
        output_image_path = output_path / Path(image_path.name)
        if not output_image_path.is_file():
            if image_path.name.endswith('GT.tiff') and copy_gt:
                shutil.copyfile(image_path, output_image_path)
            elif image_path.name.endswith('IM.tiff'):
                reader = AICSImage(image_path)
                img = reader.get_image_data('YX')
                OmeTiffWriter.save(wasteful_compression(img,compression), output_image_path, dim_order='YX')  
    
def extract_origin_dir(path):
    output_path = path / Path('original')
    output_path.mkdir(parents=True, exist_ok=True)
    for image_path in path.glob('*IM.tiff'):
        output_image_path = output_path / Path(image_path.name)
        if not output_image_path.is_file():
            shutil.copyfile(image_path, output_image_path)

for compression in compression_techniques:
    compress_dir(compression,train_path_2d,True)
    compress_dir(compression,holdout_path_2d,False)
    
extract_origin_dir(holdout_path_2d)
compression_techniques.append('original')

# Deep Leanring Compression

In [9]:
!nvidia-smi
import os
os.environ['CUDA_VISIBLE_DEVICES'] = "3"
!export CUDA_VISIBLE_DEVICES=3 

Wed May 10 18:10:34 2023       
+-----------------------------------------------------------------------------+
| NVIDIA-SMI 470.161.03   Driver Version: 470.161.03   CUDA Version: 11.4     |
|-------------------------------+----------------------+----------------------+
| GPU  Name        Persistence-M| Bus-Id        Disp.A | Volatile Uncorr. ECC |
| Fan  Temp  Perf  Pwr:Usage/Cap|         Memory-Usage | GPU-Util  Compute M. |
|                               |                      |               MIG M. |
|===============================+======================+======================|
|   0  NVIDIA A100-SXM...  Off  | 00000000:0E:00.0 Off |                    0 |
| N/A   28C    P0    53W / 400W |      0MiB / 40536MiB |      0%      Default |
|                               |                      |             Disabled |
+-------------------------------+----------------------+----------------------+
|   1  NVIDIA A100-SXM...  Off  | 00000000:13:00.0 Off |                    0 |
| N/A   

In [10]:
from compressai.zoo.image import cfgs
from compressai.zoo import image_models

configurations=[]
for model in image_models.keys():
    for metric in ['mse','ms-ssim']:
        configurations.append((model,max(cfgs[model]),metric))

for setting in configurations:
    for image in holdout_path_2d.glob('*IM*.tiff'): 
        model_name= setting[0]+'_'+setting[2]+'_'+str(setting[1])+'_RGB'
        path_encoded= image.parent/model_name/str(image.stem+'_encoded')
        path_encoded.parent.mkdir(exist_ok=True)
        path_decoded= image.parent/model_name/str(image.stem+'_decoded.tiff')
        path_decoded.parent.mkdir(exist_ok=True)
        if not path_decoded.is_file():
            !python3 codec.py encode {image} -o {path_encoded} --model {setting[0]} -q {setting[1]} -m {setting[2]} --cuda
            !python3 codec.py decode {path_encoded} -o {path_decoded} --cuda

In [ ]:
!run_im2im --config my_im2im_config_train_generator.yaml 
!run_im2im --config my_im2im_config_train.yaml 

In [6]:
prediction= 'prediction_JPEGXR' 

for dir in [i for i in holdout_path_2d.glob('*') if i.is_dir() and any(j.is_file() for j in i.glob('*'))]:
    Path(dir/prediction).mkdir(exist_ok=True)
    !echo {dir.name}
    !run_im2im --config im2im/2D/my_im2im_config_inference.yaml --model.checkpoint im2im/2D/train_best_JPEGXR.ckpt --data.inference_input.dir {dir} --data.inference_output.path {dir/prediction}

JPEGXR
2023-03-28 07:26:10,576 - Created a temporary directory at /tmp/tmpcra2vj3z
2023-03-28 07:26:10,577 - Writing /tmp/tmpcra2vj3z/_remote_module_non_scriptable.py
loading configuration from im2im/2D/my_im2im_config_inference.yaml ...
configuration loading is completed
98 files are found at data/labelfree2D/FBL/holdout/JPEGXR
Reading the image 0/98
data/labelfree2D/FBL/holdout/JPEGXR/7638_IM.tiff
Predicting the image
Reading the image 1/98
data/labelfree2D/FBL/holdout/JPEGXR/7652_IM.tiff
Predicting the image
Reading the image 2/98
data/labelfree2D/FBL/holdout/JPEGXR/7662_IM.tiff
Predicting the image
Reading the image 3/98
data/labelfree2D/FBL/holdout/JPEGXR/7664_IM.tiff
Predicting the image
Reading the image 4/98
data/labelfree2D/FBL/holdout/JPEGXR/7666_IM.tiff
Predicting the image
Reading the image 5/98
data/labelfree2D/FBL/holdout/JPEGXR/7670_IM.tiff
Predicting the image
Reading the image 6/98
data/labelfree2D/FBL/holdout/JPEGXR/7683_IM.tiff
Predicting the image
Reading the image 

In [7]:
prediction= 'prediction_JPEGXR' 

for dir in [i for i in holdout_path_2d.glob('*') if i.is_dir() and any(j.is_file() for j in i.glob('*'))]:
    Path(dir/prediction).mkdir(exist_ok=True)
    !echo {dir.name}
    !run_im2im --config im2im/2D/my_im2im_config_inference.yaml --model.checkpoint im2im/2D/train_best_JPEGXR.ckpt --data.inference_input.dir {dir} --data.inference_output.path {dir/prediction}

JPEGXR
2023-03-28 07:35:28,083 - Created a temporary directory at /tmp/tmpugdiley9
2023-03-28 07:35:28,083 - Writing /tmp/tmpugdiley9/_remote_module_non_scriptable.py
loading configuration from im2im/2D/my_im2im_config_inference.yaml ...
configuration loading is completed
98 files are found at data/labelfree2D/FBL/holdout/JPEGXR
Reading the image 0/98
data/labelfree2D/FBL/holdout/JPEGXR/7638_IM.tiff
Predicting the image
Reading the image 1/98
data/labelfree2D/FBL/holdout/JPEGXR/7652_IM.tiff
Predicting the image
Reading the image 2/98
data/labelfree2D/FBL/holdout/JPEGXR/7662_IM.tiff
Predicting the image
Reading the image 3/98
data/labelfree2D/FBL/holdout/JPEGXR/7664_IM.tiff
Predicting the image
Reading the image 4/98
data/labelfree2D/FBL/holdout/JPEGXR/7666_IM.tiff
Predicting the image
Reading the image 5/98
data/labelfree2D/FBL/holdout/JPEGXR/7670_IM.tiff
Predicting the image
Reading the image 6/98
data/labelfree2D/FBL/holdout/JPEGXR/7683_IM.tiff
Predicting the image
Reading the image 

# Evaluation 

In [11]:
import pandas as pd
import warnings
warnings.simplefilter(action='ignore', category=FutureWarning)
import numpy as np
from aicsimageio import AICSImage
from aicsimageio.writers import OmeTiffWriter
from pathlib import Path
import os
import sys
import numpy as np
from skimage.metrics import structural_similarity as ssim
import monai
import torch

def normalizeItensity(image):
    # Convert the image data to a floating-point data type
    img = image.astype(np.float32)
    # Convert the image to a toch Tensor
    img = torch.from_numpy(img)
    # Normalize the intensity of the image using the MONAI NormalizeIntensity transform
    normalize_intensity = monai.transforms.NormalizeIntensity()
    img_normalized = normalize_intensity(img)
    # Convert the normalized image back to a numpy array
    return img_normalized.numpy()

def compression_ratio_space_savings(image_path,values=924*624 ,bits=16):
    ratio= (values*bits) / (os.stat(image_path).st_size*8)
    savings= (1-(( os.stat(image_path).st_size*8) / (values*bits) ))
    return ratio, savings

def compare_images(path1, path2, gt=False):
    # Load the two images
    image1 = AICSImage(path1).get_image_data('YX') 
    image2 = AICSImage(path2).get_image_data('YX') 
    if gt:
        # image1 = image1.astype(np.float32)
        # # Scale the values in image1 to the range [0, 65535]
        # scaled_image = (image1 / np.max(image1) * 65535).round().astype(np.uint16)
        # image1 = scaled_image
        image2 = normalizeItensity(image2)
        #print(type(image1[0][0]), type(image2[0][0]))
    # Calculate metrics
    mse = np.mean((image1 - image2) ** 2)
    ssim_value = ssim(image1, image2, data_range=image1.max() - image1.min())
    corr = np.corrcoef(image1.ravel(), image2.ravel())[0, 1]
    psnr = 10 * np.log10(255**2 / (mse + 0.000001))
    return mse, ssim_value, corr, psnr

In [12]:
table_data = []
for dir in [i for i in holdout_path_2d.glob('*') if i.is_dir() and any(j.is_file() for j in i.glob('*'))]:
    space_savings = []
    compression_ratios = []
    pattern = '*_encoded'
    if dir.name in compression_techniques:
        pattern= '*.tiff'
    for image in dir.glob(pattern):
        r, s = compression_ratio_space_savings(image)
        space_savings.append(s)
        compression_ratios.append(r)
    table_data.append({
        'compressiontechnique': dir.name.replace('_','-'),
        'compressionratiomean': np.mean(compression_ratios),
        'compressionratioaverage': np.average(compression_ratios),
        'compressionratiomax': np.max(compression_ratios),
        'compressionratiomin': np.min(compression_ratios),
        'spacesavingmean': np.mean(space_savings),
        'spacesavingaverage': np.average(space_savings),
        'spacesavingmax': np.max(space_savings),
        'spacesavingmin': np.min(space_savings)
    })

df = pd.DataFrame(table_data)
df = df.round(4)
df.to_csv('compression.csv', index=False, sep=",", decimal=".")

In [13]:
import pandas as pd


table_data = []
for dir in [i for i in holdout_path_2d.glob('*') if i.is_dir() and any(j.is_file() for j in i.glob('*'))]: 
    mses = []
    ssim_values = []
    corrs = []
    psnrs = []
    for image in dir.glob('*.tiff'):
        mse, ssim_value, corr, psnr = compare_images(image,dir.parent/ image.name.replace('_decoded','') )
        mses.append(mse)
        ssim_values.append(ssim_value)
        corrs.append(corr)
        psnrs.append(psnr)
    table_data.append({
        'dirname': dir.name.replace('_','-'),
        'msemean': np.mean(mses),
        'mseaverage': np.average(mses),
        'msehighest': np.max(mses),
        'mselowest': np.min(mses),
        'ssimmean': np.mean(ssim_values),
        'ssimaverage': np.average(ssim_values),
        'ssimhighest': np.max(ssim_values),
        'ssimlowest': np.min(ssim_values),
        'correlationmean': np.mean(corrs),
        'correlationaverage': np.average(corrs),
        'correlationhighest': np.max(corrs),
        'correlationlowest': np.min(corrs),
        'psnrmean': np.mean(psnrs),
        'psnraverage': np.average(psnrs),
        'psnrhighest': np.max(psnrs),
        'psnrlowest': np.min(psnrs)
    })
df = pd.DataFrame(table_data)
df = df.round(4)
df.to_csv('metrics_input.csv', index=False, sep=",", decimal=".")

/mnt/eternus/anaconda3_shared/envs/js_compression/lib/python3.9/site-packages/numpy/lib/function_base.py:2853: RuntimeWarning: invalid value encountered in divide
  c /= stddev[:, None]
/mnt/eternus/anaconda3_shared/envs/js_compression/lib/python3.9/site-packages/numpy/lib/function_base.py:2854: RuntimeWarning: invalid value encountered in divide
  c /= stddev[None, :]
/mnt/eternus/anaconda3_shared/envs/js_compression/lib/python3.9/site-packages/numpy/lib/function_base.py:2853: RuntimeWarning: invalid value encountered in divide
  c /= stddev[:, None]
/mnt/eternus/anaconda3_shared/envs/js_compression/lib/python3.9/site-packages/numpy/lib/function_base.py:2854: RuntimeWarning: invalid value encountered in divide
  c /= stddev[None, :]


In [14]:
table_data = []
for dir in [i for i in holdout_path_2d.glob('*') if i.is_dir() and any(j.is_file() for j in i.glob('*'))]:  
    print(dir.name)
    mses = []
    ssim_values = []
    corrs = []
    psnrs = []
    for image in Path(dir/'prediction').glob('*.tiff'):
        mse, ssim_value, corr, psnr = compare_images(image,dir.parent/ image.name.replace('_decoded','').replace('_pred','').replace('IM','GT') ,gt=True)
        mses.append(mse)
        ssim_values.append(ssim_value)
        corrs.append(corr)
        psnrs.append(psnr)
    table_data.append({
        'dirname': dir.name.replace('_','-'),
        'msemean': np.mean(mses),
        'mseaverage': np.average(mses),
        'msehighest': np.max(mses),
        'mselowest': np.min(mses),
        'ssimmean': np.mean(ssim_values),
        'ssimaverage': np.average(ssim_values),
        'ssimhighest': np.max(ssim_values),
        'ssimlowest': np.min(ssim_values),
        'correlationmean': np.mean(corrs),
        'correlationaverage': np.average(corrs),
        'correlationhighest': np.max(corrs),
        'correlationlowest': np.min(corrs),
        'psnrmean': np.mean(psnrs),
        'psnraverage': np.average(psnrs),
        'psnrhighest': np.max(psnrs),
        'psnrlowest': np.min(psnrs)
    })
df = pd.DataFrame(table_data)
df = df.round(4)
df.to_csv('metrics_prediction_gt.csv', index=False, sep=",", decimal=".")

JPEGXR
LERC
bmshj2018-factorized_mse_8_RGB
bmshj2018-factorized-relu_mse_8_RGB
mbt2018-mean_mse_8_RGB
cheng2020-attn_ms-ssim_6_RGB
cheng2020-anchor_6_mse


/mnt/eternus/anaconda3_shared/envs/js_compression/lib/python3.9/site-packages/numpy/core/fromnumeric.py:3432: RuntimeWarning: Mean of empty slice.
  return _methods._mean(a, axis=axis, dtype=dtype,
/mnt/eternus/anaconda3_shared/envs/js_compression/lib/python3.9/site-packages/numpy/core/_methods.py:190: RuntimeWarning: invalid value encountered in double_scalars
  ret = ret.dtype.type(ret / rcount)
/mnt/eternus/anaconda3_shared/envs/js_compression/lib/python3.9/site-packages/numpy/lib/function_base.py:518: RuntimeWarning: Mean of empty slice.
  avg = a.mean(axis, **keepdims_kw)


ValueError: zero-size array to reduction operation maximum which has no identity

In [ ]:
table_data = []
for dir in [i for i in holdout_path_2d.glob('*') if i.is_dir() and any(j.is_file() for j in i.glob('*'))]:  
    mses = []
    ssim_values = []
    corrs = []
    psnrs = []
    for image in Path(dir/'prediction').glob('*.tiff'):
        mse, ssim_value, corr, psnr = compare_images(image,dir.parent/ 'original' / 'prediction' /image.name.replace('_decoded','') )
        mses.append(mse)
        ssim_values.append(ssim_value)
        corrs.append(corr)
        psnrs.append(psnr)
    table_data.append({
        'dirname': dir.name.replace('_','-'),
        'msemean': np.mean(mses),
        'mseaverage': np.average(mses),
        'msehighest': np.max(mses),
        'mselowest': np.min(mses),
        'ssimmean': np.mean(ssim_values),
        'ssimaverage': np.average(ssim_values),
        'ssimhighest': np.max(ssim_values),
        'ssimlowest': np.min(ssim_values),
        'correlationmean': np.mean(corrs),
        'correlationaverage': np.average(corrs),
        'correlationhighest': np.max(corrs),
        'correlationlowest': np.min(corrs),
        'psnrmean': np.mean(psnrs),
        'psnraverage': np.average(psnrs),
        'psnrhighest': np.max(psnrs),
        'psnrlowest': np.min(psnrs)
    })
df = pd.DataFrame(table_data)
df = df.round(4)
df.to_csv('metrics_prediction_original_prediction.csv', index=False, sep=",", decimal=".")

In [ ]:
!pip install matplotlib-scalebar

In [7]:
%matplotlib inline
import numpy as np
import matplotlib.pyplot as plt 
from mmv_im2im.preprocessing import transforms
from monai.transforms import NormalizeIntensity, CenterSpatialCrop, Compose
from skimage.metrics import structural_similarity as ssim
from skimage.metrics import mean_squared_error
import scipy as sc
import random
from matplotlib.patches import Rectangle
from matplotlib_scalebar.scalebar import ScaleBar
import copy
import monai
import torch

# input= dir structure: types and raw data
def plot_data(root_dir):
    #Collect all used methods
    print(root_dir)
    random_image= random.choice(list(root_dir.glob('*_IM.tiff')))
    #random_image_backup= copy.deepcopy(random_image)
    print(random_image)
    for dir in [i for i in holdout_path_2d.glob('*') if (i / random_image.name).exists() or (i / str(random_image.stem+'_decoded.tiff')).exists()   ]:
        print(dir)  
        #plt.figure(figsize=(20,9)) # specifying the overall grid size
        plt.figure(figsize=(10, 6), dpi=300)
        plt.subplots_adjust(wspace=0.1, hspace=0.25)
        #plt.suptitle(dir.name) # or plt.suptitle('Main title')  
        input_img = AICSImage(random_image).get_image_data("YX")
        

        if dir.name in compression_techniques:
            compression_img = AICSImage(dir / random_image.name).get_image_data("YX")
        else:
            compression_img = AICSImage(dir / str(random_image.stem+'_decoded.tiff')).get_image_data("YX")

        if dir.name in compression_techniques:
            prediction_img = AICSImage(dir / 'prediction' / Path(random_image.stem+'_pred.tiff')).get_image_data("YX")
        else:
            prediction_img = AICSImage(dir / 'prediction' / Path(random_image.stem+'_decoded_pred.tiff')).get_image_data("YX")
        groundtrouth_img = AICSImage(root_dir / random_image.name.replace('IM','GT')).get_image_data("YX")
        original_prediction = AICSImage(dir.parent/ 'original' / 'prediction' / Path(random_image.stem+'_pred.tiff')).get_image_data("YX")

        # Plot
        plt.subplot(2, 2, 1)
        plt.imshow(input_img, cmap='gray')
        plt.title(f'Input ' + str(np.shape(input_img)))
        scalebar1 = ScaleBar(0.108333, 'um', frameon=False, color='white')
        plt.gca().add_artist(scalebar1)

        plt.subplot(2, 2, 2)
        plt.imshow(compression_img, cmap='gray')
        plt.title('Compression ' + str(np.shape(compression_img)))
        scalebar2 = ScaleBar(0.108333, 'um', frameon=False, color='white')
        plt.gca().add_artist(scalebar2)

        plt.subplot(2, 2, 3)
        plt.imshow(prediction_img, cmap='gray')
        plt.title('Prediction ' + str(np.shape(prediction_img)))
        scalebar3 = ScaleBar(0.108333, 'um', frameon=False, color='white')
        plt.gca().add_artist(scalebar3)

        # plt.subplot(2, 2, 5)
        # plt.imshow(original_prediction, cmap='gray')
        # plt.title('Prediction on uncompressed Data ' + str(np.shape(original_prediction)))
        # scalebar4 = ScaleBar(1, 'um', frameon=False, color='white')
        # plt.gca().add_artist(scalebar4)

        plt.subplot(2, 2, 4)
        gt = NormalizeIntensity()(groundtrouth_img)
        plt.imshow(gt, cmap='gray')
        plt.title('Groundtrouth (Normalized Intensity) ' + str(np.shape(groundtrouth_img)))
        scalebar5 = ScaleBar(0.108333, 'um', frameon=False, color='white')
        plt.gca().add_artist(scalebar5)

        plt.savefig(dir.name + '_plot.png')

    #plt.show() 
    


plot_data(holdout_path_2d)

data/labelfree2D/FBL/holdout
data/labelfree2D/FBL/holdout/8896_IM.tiff
data/labelfree2D/FBL/holdout/JPEGXR
data/labelfree2D/FBL/holdout/LERC
data/labelfree2D/FBL/holdout/bmshj2018-factorized_mse_8_RGB
data/labelfree2D/FBL/holdout/bmshj2018-factorized-relu_mse_8_RGB
data/labelfree2D/FBL/holdout/mbt2018-mean_mse_8_RGB
data/labelfree2D/FBL/holdout/cheng2020-attn_ms-ssim_6_RGB
data/labelfree2D/FBL/holdout/bmshj2018-factorized-relu_ms-ssim_8_RGB
data/labelfree2D/FBL/holdout/cheng2020-anchor_ms-ssim_6_RGB
data/labelfree2D/FBL/holdout/mbt2018-mean_ms-ssim_8_RGB
data/labelfree2D/FBL/holdout/bmshj2018-hyperprior_mse_8_RGB
data/labelfree2D/FBL/holdout/mbt2018_mse_8_RGB
data/labelfree2D/FBL/holdout/JPEG_2000_LOSSY
data/labelfree2D/FBL/holdout/original
data/labelfree2D/FBL/holdout/bmshj2018-factorized_ms-ssim_8_RGB
data/labelfree2D/FBL/holdout/bmshj2018-hyperprior_ms-ssim_8_RGB
data/labelfree2D/FBL/holdout/cheng2020-attn_mse_6_RGB
data/labelfree2D/FBL/holdout/mbt2018_ms-ssim_8_RGB
data/labelfree2D

In [6]:
import csv

# Specify the path to the metadata CSV file
csv_file = '/mnt/eternus/users/Jan/data/CompressAI/examples/data/labelfree3D/FBL/meta.csv'

# Specify the key you want to extract
target_key = 'scale_micron'

# Open the CSV file
with open(csv_file, 'r') as file:
    # Create a CSV reader object
    reader = csv.DictReader(file)
    
    # Iterate over each row in the CSV file
    for row in reader:
        # Extract the value of the target key from the current row
        value = row.get(target_key)
        
        # Do further processing with the extracted value
        if value is not None:
            print(value)
            
#0.108333

[0.108333, 0.108333, 0.108333]
[0.108333, 0.108333, 0.108333]
[0.108333, 0.108333, 0.108333]
[0.108333, 0.108333, 0.108333]
[0.108333, 0.108333, 0.108333]
[0.108333, 0.108333, 0.108333]
[0.108333, 0.108333, 0.108333]
[0.108333, 0.108333, 0.108333]
[0.108333, 0.108333, 0.108333]
[0.108333, 0.108333, 0.108333]
[0.108333, 0.108333, 0.108333]
[0.108333, 0.108333, 0.108333]
[0.108333, 0.108333, 0.108333]
[0.108333, 0.108333, 0.108333]
[0.108333, 0.108333, 0.108333]
[0.108333, 0.108333, 0.108333]
[0.108333, 0.108333, 0.108333]
[0.108333, 0.108333, 0.108333]
[0.108333, 0.108333, 0.108333]
[0.108333, 0.108333, 0.108333]
[0.108333, 0.108333, 0.108333]
[0.108333, 0.108333, 0.108333]
[0.108333, 0.108333, 0.108333]
[0.108333, 0.108333, 0.108333]
[0.108333, 0.108333, 0.108333]
[0.108333, 0.108333, 0.108333]
[0.108333, 0.108333, 0.108333]
[0.108333, 0.108333, 0.108333]
[0.108333, 0.108333, 0.108333]
[0.108333, 0.108333, 0.108333]
[0.108333, 0.108333, 0.108333]
[0.108333, 0.108333, 0.108333]
[0.10833

In [ ]:
import numpy as np
import matplotlib.pyplot as plt
import random
from matplotlib_scalebar.scalebar import ScaleBar

def diff_data_color(root_dir):
    print(root_dir)
    random_image= random.choice(list(root_dir.glob('*_IM.tiff')))
    print(random_image)
    for dir in [i for i in holdout_path_2d.glob('*') if (i / random_image.name).exists() or (i / str(random_image.stem+'_decoded.tiff')).exists()   ]:
        print(dir)  
        plt.figure(figsize=(10, 6), dpi=300)
        input_img = AICSImage(random_image).get_image_data("YX")
        if dir.name in compression_techniques:
            compression_img = AICSImage(dir / random_image.name).get_image_data("YX")
        else:
            compression_img = AICSImage(dir / str(random_image.stem+'_decoded.tiff')).get_image_data("YX")

        # Subtract image2 from image1
        diff_image = np.abs(input_img - compression_img)
        
        # Plot the difference image
        plt.imshow(diff_image, cmap='hot', vmin=0, vmax=np.max(diff_image))
        plt.colorbar()
        scalebar = ScaleBar(0.108333, 'um', frameon=True, color='black')
        plt.gca().add_artist(scalebar)

        plt.savefig(dir.name + '_diff_color.png')

def diff_data_gray(root_dir):
    print(root_dir)
    random_image= random.choice(list(root_dir.glob('*_IM.tiff')))
    print(random_image)
    for dir in [i for i in holdout_path_2d.glob('*') if (i / random_image.name).exists() or (i / str(random_image.stem+'_decoded.tiff')).exists()   ]:
        print(dir)  
        plt.figure(figsize=(10, 6), dpi=300)
        input_img = AICSImage(random_image).get_image_data("YX")
        if dir.name in compression_techniques:
            compression_img = AICSImage(dir / random_image.name).get_image_data("YX")
        else:
            compression_img = AICSImage(dir / str(random_image.stem+'_decoded.tiff')).get_image_data("YX")

        # Subtract image2 from image1
        diff_image = np.abs(input_img - compression_img)
        
        # Plot the difference image
        plt.imshow(diff_image, cmap='gray', vmin=0, vmax=np.max(diff_image))
        scalebar = ScaleBar(0.108333, 'um', frameon=True, color='black')
        plt.gca().add_artist(scalebar)

        plt.savefig(dir.name + '_diff_gray.png')

diff_data_gray(holdout_path_2d)
diff_data_color(holdout_path_2d)

NameError: name 'holdout_path_2d' is not defined